# Challenge Machine Learning 
# Florian André 3B IA

Dataset utilisé : Backpack Prediction Challenge trouvé sur Kaggle 
URL : https://www.kaggle.com/competitions/playground-series-s5e2/overview


## Explication du dataset
Ce dataset est composé de 4 fichiers 
- train.csv : notre dataset d'entraînement
- train_extra.csv : dataset d'entraînement supplémentaire (avec erreurs)
- test.csv : dataset pour tester notre modèle
- sample_submission : dataset contenant l'id des sacs testés ainsi que leur prédiction de prix

In [37]:
## Liste des bibliothèques utilisées
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns
import numpy as np

## Importation et nettoyage des données

Nous allons dans un premier temps importer les données d'entraînement de notre fichier train.csv

In [38]:
path = "/home/florian-andr/Downloads/playground-series-s5e2"
df_train = pd.read_csv(f"{path}/train.csv")
df_test = pd.read_csv(f"{path}/test.csv")
print(df_train.head())
print(df_train.shape)
print(df_test.head())
print(df_test.shape)

   id         Brand Material    Size  Compartments Laptop Compartment  \
0   0      Jansport  Leather  Medium           7.0                Yes   
1   1      Jansport   Canvas   Small          10.0                Yes   
2   2  Under Armour  Leather   Small           2.0                Yes   
3   3          Nike    Nylon   Small           8.0                Yes   
4   4        Adidas   Canvas  Medium           1.0                Yes   

  Waterproof      Style  Color  Weight Capacity (kg)      Price  
0         No       Tote  Black             11.611723  112.15875  
1        Yes  Messenger  Green             27.078537   68.88056  
2         No  Messenger    Red             16.643760   39.17320  
3         No  Messenger  Green             12.937220   80.60793  
4        Yes  Messenger  Green             17.749338   86.02312  
(300000, 11)
       id   Brand Material    Size  Compartments Laptop Compartment  \
0  300000    Puma  Leather   Small           2.0                 No   
1  300001 

Procédons maintenant au nettoyage des données : en effet, certaines lignes comportent des valeurs nulles qu'il faut éliminer avant d'effectuer l'entraînement

In [39]:
df_train.dropna(inplace=True)
print(df_train.head())
print(df_train.shape)

   id         Brand Material    Size  Compartments Laptop Compartment  \
0   0      Jansport  Leather  Medium           7.0                Yes   
1   1      Jansport   Canvas   Small          10.0                Yes   
2   2  Under Armour  Leather   Small           2.0                Yes   
3   3          Nike    Nylon   Small           8.0                Yes   
4   4        Adidas   Canvas  Medium           1.0                Yes   

  Waterproof      Style  Color  Weight Capacity (kg)      Price  
0         No       Tote  Black             11.611723  112.15875  
1        Yes  Messenger  Green             27.078537   68.88056  
2         No  Messenger    Red             16.643760   39.17320  
3         No  Messenger  Green             12.937220   80.60793  
4        Yes  Messenger  Green             17.749338   86.02312  
(246686, 11)


Maintenant, nous allons séparer le dataset en 2 parties (1 train et 1 test)

In [40]:
# Split the data
train_data = df_train.sample(frac=0.6, random_state=42)
test_data = df_train.sample(frac=0.4, random_state=42)
X_train = train_data.drop(columns=["id", "Price"])
y_train = train_data["Price"]
X_test = test_data.drop(columns=["id", "Price"])
y_test = test_data["Price"]


Il nous faut aussi éliminer les valeurs aberrantes sur "Weight Capacity (kg)" et "Price". On utilisera le z-score pour procéder à l'élimination de ces valeurs. 
Nous avons divisé le dataset en 2 quartiles (25% et 75%) sur la capacité de poids et le prix. Chaque valeur qui dépassera de 50% l'écart inter-quartile sera écartée
du dataset d'entraînement final.

In [41]:
QW1 = df_train["Weight Capacity (kg)"].quantile(0.25)
QW3 = df_train["Weight Capacity (kg)"].quantile(0.75)
IQWR = QW3 - QW1

QP1 = df_train["Price"].quantile(0.25)
QP3 = df_train["Price"].quantile(0.75)
IQPR = QP3 - QP1

threshold = 0.5
df_train = df_train[(df_train["Weight Capacity (kg)"] > (QW1 - threshold * IQWR)) & (df_train["Weight Capacity (kg)"] < (QW3 + threshold * IQWR))]
df_train = df_train[(df_train["Price"] > (QP1 - threshold * IQPR)) & (df_train["Price"] < (QP3 + threshold * IQPR))]
print(df_train.shape)

(234381, 11)


In [42]:
X_train = train_data.drop(columns=["id", "Price"])
y_train = train_data["Price"]
X_test = test_data.drop(columns=["Price"])
y_test = test_data["Price"]

## Prétraitement des données (Data pre-processing)
Maintenant que notre dataset d'entraînement a été nettoyé, il faut prétraiter nos données via le feature engineering. On va utiliser une Random Forest ainsi que la méthode Feature Importance afin de ne garder que les variables les plus pertinentes pour notre modèle

On doit d'abord encoder les variables catégorielles de notre dataset

In [43]:
# Encode the categorical variables 
X_train["Brand"] = pd.factorize(X_train["Brand"])[0]
X_train["Material"] = pd.factorize(X_train["Material"])[0]
X_train["Size"] = pd.factorize(X_train["Size"])[0]
X_train["Laptop Compartment"] = pd.factorize(X_train["Laptop Compartment"])[0]
X_train["Waterproof"] = pd.factorize(X_train["Waterproof"])[0]
X_train["Style"] = pd.factorize(X_train["Style"])[0]
X_train["Color"] = pd.factorize(X_train["Color"])[0]


X_test["Brand"] = pd.factorize(X_test["Brand"])[0]
X_test["Material"] = pd.factorize(X_test["Material"])[0]
X_test["Size"] = pd.factorize(X_test["Size"])[0]
X_test["Laptop Compartment"] = pd.factorize(X_test["Laptop Compartment"])[0]
X_test["Waterproof"] = pd.factorize(X_test["Waterproof"])[0]
X_test["Style"] = pd.factorize(X_test["Style"])[0]
X_test["Color"] = pd.factorize(X_test["Color"])[0]



# Print the dataframe to verify
print(df_train.head())


   id         Brand Material    Size  Compartments Laptop Compartment  \
0   0      Jansport  Leather  Medium           7.0                Yes   
1   1      Jansport   Canvas   Small          10.0                Yes   
2   2  Under Armour  Leather   Small           2.0                Yes   
3   3          Nike    Nylon   Small           8.0                Yes   
4   4        Adidas   Canvas  Medium           1.0                Yes   

  Waterproof      Style  Color  Weight Capacity (kg)      Price  
0         No       Tote  Black             11.611723  112.15875  
1        Yes  Messenger  Green             27.078537   68.88056  
2         No  Messenger    Red             16.643760   39.17320  
3         No  Messenger  Green             12.937220   80.60793  
4        Yes  Messenger  Green             17.749338   86.02312  


Une fois les variables encodées, il est possible d'utiliser RandomForest pour avoir la Feature Importance. Comme la sortie n'est pas associée à une classe, il faut utiliser RandomForestRegressor.

In [44]:
X_test

id  Brand  Material  Size  Compartments  Laptop Compartment  \
70197    70197      0         0     0           3.0                   0   
211706  211706      1         1     0           2.0                   1   
65359    65359      1         2     0           8.0                   0   
226593  226593      0         3     1           2.0                   0   
93268    93268      2         2     1           5.0                   1   
...        ...    ...       ...   ...           ...                 ...   
118021  118021      4         3     1           3.0                   0   
72194    72194      3         3     0           6.0                   1   
296792  296792      0         3     2           3.0                   1   
185105  185105      2         0     1           8.0                   0   
56101    56101      4         1     1           8.0                   0   

        Waterproof  Style  Color  Weight Capacity (kg)  
70197            0      0      0             20.034746  
211706           0      0      1              8.743295  
65359            0      1      2             28.593976  
226593           1      2      3             15.188859  
93268            0      0      4             11.587306  
...            ...    ...    ...                   ...  
118021           0      2      2             10.574090  
72194            0      1      3             12.637730  
296792           0      2      5              6.977963  
185105           1      1      1             25.287812  
56101            1      1      1             15.485371  

[98674 rows x 10 columns]

In [45]:
from sklearn.ensemble import RandomForestRegressor

# Train the RandomForestRegressor
rf = RandomForestRegressor(n_estimators=100, random_state=42)
rf.fit(X_train, y_train)

# Get feature importances
feature_importances = rf.feature_importances_


In [46]:
importance_df = pd.DataFrame({
    'Feature': X_train.columns,
    'Importance': feature_importances
})

In [47]:
importance_df

Feature  Importance
0                 Brand    0.079320
1              Material    0.039640
2                  Size    0.061688
3          Compartments    0.130414
4    Laptop Compartment    0.038698
5            Waterproof    0.037378
6                 Style    0.062827
7                 Color    0.079860
8  Weight Capacity (kg)    0.470174

In [48]:
top_n_features = 6
top_features = importance_df.head(top_n_features)['Feature'].values

On peut enfin réduire le dataset d'entrainement afin qu'il ne contienne que les features nécessaires trouvées avec Random Forest

In [49]:
X_train = X_train[top_features]

## Entraînement du modèle

une fois les features les plus importantes sélectionnées, il est possible d'entraîner notre modèle à l'aide d'un perceptron multi-couches (MLP)

In [50]:
from sklearn.neural_network import MLPRegressor
from sklearn.preprocessing import StandardScaler

scaler = StandardScaler()

X_train = scaler.fit_transform(X_train)

rgr = MLPRegressor(random_state=42, solver='adam')
rgr.fit(X_train, y_train)


MLPRegressor(random_state=42)

## Evaluation du modèle
Une fois le modèle entraîné, il ne nous reste plus qu'à l'évaluer sur le dataset de test et à sauvegarder les prédictions dans le fichier sample_submission.csv

In [52]:
import pandas as pd

# Select the top features from X_test
X_test_selected = X_test[top_features]
X_test_selected = scaler.transform(X_test_selected)
X_test_selected_scaled = pd.DataFrame(X_test_selected, columns=top_features)
y_pred = rgr.predict(X_test_selected)

# Print the id and predicted values
for id, pred in zip(X_test["id"], y_pred):
	print(f"ID: {id}, Predicted Price: {pred}")

# Sauvegarde dans le fichier sample_submission.csv 
output = pd.DataFrame({'id': X_test["id"], 'price': y_pred})
output.to_csv(f'{path}/sample_submission.csv', index=False)

ID: 70197, Predicted Price: 81.31445801608655
ID: 211706, Predicted Price: 82.71277010282259
ID: 65359, Predicted Price: 81.42666139796326
ID: 226593, Predicted Price: 81.11394019042395
ID: 93268, Predicted Price: 83.2118249987407
ID: 82142, Predicted Price: 81.74719171690978
ID: 17685, Predicted Price: 81.72770260335412
ID: 273696, Predicted Price: 82.18451981801847
ID: 132485, Predicted Price: 83.25152657236731
ID: 23132, Predicted Price: 82.3585811159083
ID: 102715, Predicted Price: 82.985941101225
ID: 108620, Predicted Price: 83.25348092243661
ID: 44175, Predicted Price: 81.14212198397568
ID: 41303, Predicted Price: 82.39446250101233
ID: 259987, Predicted Price: 82.49422455625353
ID: 211484, Predicted Price: 81.69583012172362
ID: 221200, Predicted Price: 83.20370039260938
ID: 145113, Predicted Price: 83.02940346570739
ID: 215524, Predicted Price: 81.41058957506745
ID: 282862, Predicted Price: 81.55312479810911
ID: 235039, Predicted Price: 83.31430629482259
ID: 23984, Predicted Pric

L'évaluation du modèle se fait à l'aide de la méthode RMSE (Root Mean-Squared Error)

In [54]:
##Calcul RMSE

from sklearn.metrics import mean_squared_error
from math import sqrt

y_true = y_test

rmse = sqrt(mean_squared_error(y_true, y_pred))
print(rmse)


38.89362814702266


Nous obtenons à la fin un RMSE de 38.89% pour notre dataset 

## Conclusion ##

A travers ce petit challenge, nous avons pu concevoir un petit réseau de neurones afin de prédire le prix sur un dataset de sacs à dos. 